In [1]:
import tensorflow as tf
import model
from eval import resize_image, sort_poly, detect

In [14]:
from PIL import Image
import pytesseract

In [2]:
import os

import time
import datetime
import cv2
import numpy as np
import uuid
import json
import matplotlib.pyplot as plt
import functools
import logging
import collections
%matplotlib inline

logger = logging.getLogger(__name__)
logger.setLevel(logging.INFO)


In [3]:
SAVE_DIR = 'static/results'
checkpoint_path = './east_icdar2015_resnet_v1_50_rbox'


In [4]:
input_images = tf.placeholder(tf.float32, shape=[None, None, None, 3], name='input_images')
global_step = tf.get_variable('global_step', [], initializer=tf.constant_initializer(0), trainable=False)

f_score, f_geometry = model.model(input_images, is_training=False)

variable_averages = tf.train.ExponentialMovingAverage(0.997, global_step)
saver = tf.train.Saver(variable_averages.variables_to_restore())

sess = tf.Session(config=tf.ConfigProto(allow_soft_placement=True))

ckpt_state = tf.train.get_checkpoint_state(checkpoint_path)
model_path = os.path.join(checkpoint_path, os.path.basename(ckpt_state.model_checkpoint_path))
logger.info('Restore from {}'.format(model_path))
saver.restore(sess, model_path)




resnet_v1_50/block1 (?, ?, ?, 256)
resnet_v1_50/block2 (?, ?, ?, 512)
resnet_v1_50/block3 (?, ?, ?, 1024)
resnet_v1_50/block4 (?, ?, ?, 2048)
Shape of f_0 (?, ?, ?, 2048)
Shape of f_1 (?, ?, ?, 512)
Shape of f_2 (?, ?, ?, 256)
Shape of f_3 (?, ?, ?, 64)
Shape of h_0 (?, ?, ?, 2048), g_0 (?, ?, ?, 2048)
Shape of h_1 (?, ?, ?, 128), g_1 (?, ?, ?, 128)
Shape of h_2 (?, ?, ?, 64), g_2 (?, ?, ?, 64)
Shape of h_3 (?, ?, ?, 32), g_3 (?, ?, ?, 32)
INFO:tensorflow:Restoring parameters from ./east_icdar2015_resnet_v1_50_rbox/model.ckpt-49491


In [5]:
def get_host_info():
    ret = {}
    with open('/proc/cpuinfo') as f:
        ret['cpuinfo'] = f.read()

    with open('/proc/meminfo') as f:
        ret['meminfo'] = f.read()

    with open('/proc/loadavg') as f:
        ret['loadavg'] = f.read()

    return ret

In [6]:
def predictor(img):
    """
    :return: {
        'text_lines': [
            {
                'score': ,
                'x0': ,
                'y0': ,
                'x1': ,
                ...
                'y3': ,
            }
        ],
        'rtparams': {  # runtime parameters
            'image_size': ,
            'working_size': ,
        },
        'timing': {
            'net': ,
            'restore': ,
            'nms': ,
            'cpuinfo': ,
            'meminfo': ,
            'uptime': ,
        }
    }
    """
    start_time = time.time()
    rtparams = collections.OrderedDict()
    rtparams['start_time'] = datetime.datetime.now().isoformat()
    rtparams['image_size'] = '{}x{}'.format(img.shape[1], img.shape[0])
    timer = collections.OrderedDict([
        ('net', 0),
        ('restore', 0),
        ('nms', 0)
    ])

    im_resized, (ratio_h, ratio_w) = resize_image(img)
    rtparams['working_size'] = '{}x{}'.format(
        im_resized.shape[1], im_resized.shape[0])
    start = time.time()
    score, geometry = sess.run(
        [f_score, f_geometry],
        feed_dict={input_images: [im_resized[:,:,::-1]]})
    timer['net'] = time.time() - start

    boxes, timer = detect(score_map=score, geo_map=geometry, timer=timer)
    logger.info('net {:.0f}ms, restore {:.0f}ms, nms {:.0f}ms'.format(
        timer['net']*1000, timer['restore']*1000, timer['nms']*1000))

    if boxes is not None:
        scores = boxes[:,8].reshape(-1)
        boxes = boxes[:, :8].reshape((-1, 4, 2))
        boxes[:, :, 0] /= ratio_w
        boxes[:, :, 1] /= ratio_h

    duration = time.time() - start_time
    timer['overall'] = duration
    logger.info('[timing] {}'.format(duration))

    text_lines = []
    if boxes is not None:
        text_lines = []
        for box, score in zip(boxes, scores):
            box = sort_poly(box.astype(np.int32))
            if np.linalg.norm(box[0] - box[1]) < 5 or np.linalg.norm(box[3]-box[0]) < 5:
                continue
            tl = collections.OrderedDict(zip(
                ['x0', 'y0', 'x1', 'y1', 'x2', 'y2', 'x3', 'y3'],
                map(float, box.flatten())))
            tl['score'] = float(score)
            text_lines.append(tl)
    ret = {
        'text_lines': text_lines,
        'rtparams': rtparams,
        'timing': timer,
    }
    ret.update(get_host_info())
    return ret


In [33]:
def draw_illu(illu, rst):
    for t in rst['text_lines']:
        d = np.array([t['x0'], t['y0'], t['x1'], t['y1'], t['x2'],
                      t['y2'], t['x3'], t['y3']], dtype='int32')
        d = d.reshape(-1, 2)
        cv2.polylines(illu, [d], isClosed=True, color=(255, 255, 0))
    return illu

In [34]:
#img = cv2.imdecode(np.frombuffer(bio.getvalue(), dtype='uint8'), 1)
img = cv2.imread('track0061[01].png',1)
rst = predictor(img)


32 text boxes before nms


In [35]:
def save_cropped(img, rst):
    c = 0
    files = []
    for t in rst['text_lines']:
        crop_img = img[int(t['y0']):int(t['y3']), int(t['x0']):int(t['x1'])]
        filename = "demo/{}.png".format(c)
        files.append(filename)
        cv2.imwrite(filename, crop_img)
        c += 1
    return files


In [40]:
def show_results(img, rst):
    il = draw_illu(img.copy(), rst)
    plt.figure(figsize = (200,200))
    plt.imshow(cv2.cvtColor(il, cv2.COLOR_BGR2RGB))

In [36]:
files = save_cropped(img, rst)

In [37]:
def print_text(files):
    for filename in files:
        text = pytesseract.image_to_string(Image.open(filename))
        os.remove(filename)
        print(text)


In [38]:
print_text(files)

AYU-D035


In [39]:
plt.imshow(img)

In [41]:
show_results(img, rst)